In [ ]:
import os
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import load_model
from tensorflow.keras.preprocessing import image
from PIL import Image

### Bagian 1: Generate Mapping Label Otomatis ###

def generate_class_mapping(dataset_dir):
    classes = sorted([
        d for d in os.listdir(dataset_dir)
        if os.path.isdir(os.path.join(dataset_dir, d))
    ])
    index_to_label = {i: label for i, label in enumerate(classes)}
    label_to_index = {label: i for i, label in index_to_label.items()}
    return index_to_label, label_to_index

### Bagian 2: Preprocessing Gambar ###

def load_and_preprocess_image(img_path, target_size=(224, 224)):
    img = Image.open(img_path).convert('RGB')
    img = img.resize(target_size)
    img_array = image.img_to_array(img) / 255.0
    img_array = np.expand_dims(img_array, axis=0)  # (1, 224, 224, 3)
    return img_array


### Bagian 3: Fusion Confidence + Voting ###

def confidence_fusion_classification(model1_probs, model2_probs,
                                     class_mapping_model1, class_mapping_model2,
                                     alpha=0.5):
    model1_idx = np.argmax(model1_probs)
    model1_conf = model1_probs[model1_idx]
    model1_pred = class_mapping_model1.get(model1_idx, f"unknown_{model1_idx}")

    model2_idx = np.argmax(model2_probs)
    model2_conf = model2_probs[model2_idx]
    model2_pred = class_mapping_model2.get(model2_idx, f"unknown_{model2_idx}")

    if model1_pred == model2_pred:
        final = model1_pred
    else:
        weighted_score1 = alpha * model1_conf
        weighted_score2 = (1 - alpha) * model2_conf
        final = model1_pred if weighted_score1 >= weighted_score2 else model2_pred

    return final, {
        'model1_pred': model1_pred,
        'model1_conf': float(model1_conf),
        'model2_pred': model2_pred,
        'model2_conf': float(model2_conf),
        'alpha': alpha,
        'weighted_score1': float(alpha * model1_conf),
        'weighted_score2': float((1 - alpha) * model2_conf),
        'final_prediction': final
    }



In [20]:

import os
import json

def generate_class_mapping(dataset_dir, save_path='class_mapping.json'):
    classes = sorted([
        d for d in os.listdir(dataset_dir)
        if os.path.isdir(os.path.join(dataset_dir, d))
    ])
    index_to_label = {i: label for i, label in enumerate(classes)}
    label_to_index = {label: i for i, label in index_to_label.items()}

    # Gabungkan dan simpan ke file
    mapping = {
        'index_to_label': index_to_label,
        'label_to_index': label_to_index
    }

    with open(save_path, 'w', encoding='utf-8') as f:
        json.dump(mapping, f, ensure_ascii=False, indent=4)

    print(f"Class mapping disimpan ke: {save_path}")
    return index_to_label, label_to_index   

dataset_dir1 = 'Datasets/model1/training'
generate_class_mapping(dataset_dir1, save_path='class_mapping1.json')
dataset_dir2 = 'Datasets/model2/training'
generate_class_mapping(dataset_dir2, save_path='class_mapping2.json')

Class mapping disimpan ke: class_mapping1.json
Class mapping disimpan ke: class_mapping2.json


({0: 'abah',
  1: 'acara',
  2: 'agul',
  3: 'ai',
  4: 'aki',
  5: 'akur',
  6: 'angkat',
  7: 'apal',
  8: 'asup',
  9: 'asép',
  10: 'atuh',
  11: 'aya',
  12: 'ayana',
  13: 'ayeuna',
  14: 'bahar',
  15: 'bakal',
  16: 'balé',
  17: 'bandung',
  18: 'bangkong',
  19: 'bapa',
  20: 'bapak',
  21: 'baraya',
  22: 'batur',
  23: 'baé',
  24: 'bedog',
  25: 'beureum',
  26: 'bijil',
  27: 'bilatung',
  28: 'boga',
  29: 'bojo',
  30: 'bonténg',
  31: 'buah',
  32: 'bubu',
  33: 'bumi',
  34: 'butut',
  35: 'cai',
  36: 'can',
  37: 'carita',
  38: 'carék',
  39: 'cemara',
  40: 'ceuk',
  41: 'ciung',
  42: 'cokot',
  43: 'condong',
  44: 'curug',
  45: 'céri',
  46: 'damar',
  47: 'daun',
  48: 'deui',
  49: 'di',
  50: 'dibéré',
  51: 'dina',
  52: 'dipaké',
  53: 'diwaro',
  54: 'dulang',
  55: 'dulur',
  56: 'dék',
  57: 'désa',
  58: 'enéng',
  59: 'gado',
  60: 'gawir',
  61: 'gedung',
  62: 'geuning',
  63: 'geus',
  64: 'gigir',
  65: 'girang',
  66: 'gé',
  67: 'hadé',
  68: '

In [14]:
model1_path = "saved_model_finetune/fold_0/best_accuracy_model.h5"
model2_path = "saved_model_finetune_v2/fold_4/best_accuracy_model.h5"
model1_train_path = "Datasets/model1/training"
model2_train_path = "Datasets/model2/training"

# Muat Model
model1 = load_model(model1_path)
model2 = load_model(model2_path)

def predict_single_image(img_path):
    # Muat label mapping
    model1_index_to_label, _ = generate_class_mapping(model1_train_path)
    model2_index_to_label, _ = generate_class_mapping(model2_train_path)
    img_array = load_and_preprocess_image(img_path)

    # Inference
    model1_probs = model1.predict(img_array)[0]  # shape: (num_classes,)
    model2_probs = model2.predict(img_array)[0]  # shape: (num_classes,)

    # Fusion
    final_pred, details = confidence_fusion_classification(
        model1_probs, model2_probs,
        model1_index_to_label,
        model2_index_to_label,
    )

    # Output hasil
    print(f"\n📝 Hasil akhir fusion: {final_pred}")
    print("🔍 Rincian prediksi:")
    for key, val in details.items():
        print(f"{key}: {val}")

In [6]:
input_image_path = "Datasets/model2/validation/abah/6.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model1/validation/da/da (4).png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model2/validation/subuh/1.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model1/validation/ta/ta (11).png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model2/validation/téh/1.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model2/validation/ti/18.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

{0: 'a', 1: 'ba', 2: 'ca', 3: 'da', 4: 'e', 5: 'eu', 6: 'fa', 7: 'ga', 8: 'ha', 9: 'i', 10: 'ja', 11: 'ka', 12: 'kha', 13: 'la', 14: 'ma', 15: 'na', 16: 'nga', 17: 'nya', 18: 'o', 19: 'pa', 20: 'qa', 21: 'ra', 22: 'sa', 23: 'sya', 24: 'ta', 25: 'u', 26: 'va', 27: 'wa', 28: 'xa', 29: 'ya', 30: 'za', 31: 'é'}
{0: 'abah', 1: 'acara', 2: 'agul', 3: 'ai', 4: 'aki', 5: 'akur', 6: 'angkat', 7: 'apal', 8: 'asup', 9: 'asép', 10: 'atuh', 11: 'aya', 12: 'ayana', 13: 'ayeuna', 14: 'bahar', 15: 'bakal', 16: 'balé', 17: 'bandung', 18: 'bangkong', 19: 'bapa', 20: 'bapak', 21: 'baraya', 22: 'batur', 23: 'baé', 24: 'bedog', 25: 'beureum', 26: 'bijil', 27: 'bilatung', 28: 'boga', 29: 'bojo', 30: 'bonténg', 31: 'buah', 32: 'bubu', 33: 'bumi', 34: 'butut', 35: 'cai', 36: 'can', 37: 'carita', 38: 'carék', 39: 'cemara', 40: 'ceuk', 41: 'ciung', 42: 'cokot', 43: 'condong', 44: 'curug', 45: 'céri', 46: 'damar', 47: 'daun', 48: 'deui', 49: 'di', 50: 'dibéré', 51: 'dina', 52: 'dipaké', 53: 'diwaro', 54: 'dulang

In [16]:
input_image_path = "Datasets/model2/validation/ti/17.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model2/validation/téh/3.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

indexto label:  {0: 'a', 1: 'ba', 2: 'ca', 3: 'da', 4: 'e', 5: 'eu', 6: 'fa', 7: 'ga', 8: 'ha', 9: 'i', 10: 'ja', 11: 'ka', 12: 'kha', 13: 'la', 14: 'ma', 15: 'na', 16: 'nga', 17: 'nya', 18: 'o', 19: 'pa', 20: 'qa', 21: 'ra', 22: 'sa', 23: 'sya', 24: 'ta', 25: 'u', 26: 'va', 27: 'wa', 28: 'xa', 29: 'ya', 30: 'za', 31: 'é'}
label to index:  {'a': 0, 'ba': 1, 'ca': 2, 'da': 3, 'e': 4, 'eu': 5, 'fa': 6, 'ga': 7, 'ha': 8, 'i': 9, 'ja': 10, 'ka': 11, 'kha': 12, 'la': 13, 'ma': 14, 'na': 15, 'nga': 16, 'nya': 17, 'o': 18, 'pa': 19, 'qa': 20, 'ra': 21, 'sa': 22, 'sya': 23, 'ta': 24, 'u': 25, 'va': 26, 'wa': 27, 'xa': 28, 'ya': 29, 'za': 30, 'é': 31}
indexto label:  {0: 'abah', 1: 'acara', 2: 'agul', 3: 'ai', 4: 'aki', 5: 'akur', 6: 'angkat', 7: 'apal', 8: 'asup', 9: 'asép', 10: 'atuh', 11: 'aya', 12: 'ayana', 13: 'ayeuna', 14: 'bahar', 15: 'bakal', 16: 'balé', 17: 'bandung', 18: 'bangkong', 19: 'bapa', 20: 'bapak', 21: 'baraya', 22: 'batur', 23: 'baé', 24: 'bedog', 25: 'beureum', 26: 'bijil',

In [17]:
input_image_path = "Datasets/model2/validation/ai/1.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model1/training/a/a (2).png"  # Ganti sesuai file input
predict_single_image(input_image_path)

indexto label:  {0: 'a', 1: 'ba', 2: 'ca', 3: 'da', 4: 'e', 5: 'eu', 6: 'fa', 7: 'ga', 8: 'ha', 9: 'i', 10: 'ja', 11: 'ka', 12: 'kha', 13: 'la', 14: 'ma', 15: 'na', 16: 'nga', 17: 'nya', 18: 'o', 19: 'pa', 20: 'qa', 21: 'ra', 22: 'sa', 23: 'sya', 24: 'ta', 25: 'u', 26: 'va', 27: 'wa', 28: 'xa', 29: 'ya', 30: 'za', 31: 'é'}
label to index:  {'a': 0, 'ba': 1, 'ca': 2, 'da': 3, 'e': 4, 'eu': 5, 'fa': 6, 'ga': 7, 'ha': 8, 'i': 9, 'ja': 10, 'ka': 11, 'kha': 12, 'la': 13, 'ma': 14, 'na': 15, 'nga': 16, 'nya': 17, 'o': 18, 'pa': 19, 'qa': 20, 'ra': 21, 'sa': 22, 'sya': 23, 'ta': 24, 'u': 25, 'va': 26, 'wa': 27, 'xa': 28, 'ya': 29, 'za': 30, 'é': 31}
indexto label:  {0: 'abah', 1: 'acara', 2: 'agul', 3: 'ai', 4: 'aki', 5: 'akur', 6: 'angkat', 7: 'apal', 8: 'asup', 9: 'asép', 10: 'atuh', 11: 'aya', 12: 'ayana', 13: 'ayeuna', 14: 'bahar', 15: 'bakal', 16: 'balé', 17: 'bandung', 18: 'bangkong', 19: 'bapa', 20: 'bapak', 21: 'baraya', 22: 'batur', 23: 'baé', 24: 'bedog', 25: 'beureum', 26: 'bijil',

In [18]:
input_image_path = "Datasets/model2/validation/di/1.png"  # Ganti sesuai file input
predict_single_image(input_image_path)

input_image_path = "Datasets/model1/validation/da/da (1).png"  # Ganti sesuai file input
predict_single_image(input_image_path)

indexto label:  {0: 'a', 1: 'ba', 2: 'ca', 3: 'da', 4: 'e', 5: 'eu', 6: 'fa', 7: 'ga', 8: 'ha', 9: 'i', 10: 'ja', 11: 'ka', 12: 'kha', 13: 'la', 14: 'ma', 15: 'na', 16: 'nga', 17: 'nya', 18: 'o', 19: 'pa', 20: 'qa', 21: 'ra', 22: 'sa', 23: 'sya', 24: 'ta', 25: 'u', 26: 'va', 27: 'wa', 28: 'xa', 29: 'ya', 30: 'za', 31: 'é'}
label to index:  {'a': 0, 'ba': 1, 'ca': 2, 'da': 3, 'e': 4, 'eu': 5, 'fa': 6, 'ga': 7, 'ha': 8, 'i': 9, 'ja': 10, 'ka': 11, 'kha': 12, 'la': 13, 'ma': 14, 'na': 15, 'nga': 16, 'nya': 17, 'o': 18, 'pa': 19, 'qa': 20, 'ra': 21, 'sa': 22, 'sya': 23, 'ta': 24, 'u': 25, 'va': 26, 'wa': 27, 'xa': 28, 'ya': 29, 'za': 30, 'é': 31}
indexto label:  {0: 'abah', 1: 'acara', 2: 'agul', 3: 'ai', 4: 'aki', 5: 'akur', 6: 'angkat', 7: 'apal', 8: 'asup', 9: 'asép', 10: 'atuh', 11: 'aya', 12: 'ayana', 13: 'ayeuna', 14: 'bahar', 15: 'bakal', 16: 'balé', 17: 'bandung', 18: 'bangkong', 19: 'bapa', 20: 'bapak', 21: 'baraya', 22: 'batur', 23: 'baé', 24: 'bedog', 25: 'beureum', 26: 'bijil',

In [5]:
import os
import csv
import numpy as np
from sklearn.metrics import classification_report, f1_score, precision_score, recall_score, accuracy_score

def collect_image_paths(folder):
    image_paths = []
    for class_name in os.listdir(folder):
        class_dir = os.path.join(folder, class_name)
        if os.path.isdir(class_dir):
            for img_file in os.listdir(class_dir):
                if img_file.lower().endswith(('.png', '.jpg', '.jpeg')):
                    image_paths.append((os.path.join(class_dir, img_file), class_name))
    return image_paths

def predict_batch_and_evaluate(model1_val_dir, model2_val_dir, output_csv='hasil_prediksi.csv', alpha=0.5):
    # Generate label mapping
    model1_index_to_label, _ = generate_class_mapping(model1_train_path)
    model2_index_to_label, _ = generate_class_mapping(model2_train_path)

    # Kumpulkan semua data
    model1_images = collect_image_paths(model1_val_dir)
    model2_images = collect_image_paths(model2_val_dir)
    all_image_paths = model1_images + model2_images

    y_true = []
    y_pred = []
    prediction_rows = []

    for img_path, true_label in all_image_paths:
        img_array = load_and_preprocess_image(img_path)

        # Prediksi
        model1_probs = model1.predict(img_array)[0]
        model2_probs = model2.predict(img_array)[0]

        final_pred, _ = confidence_fusion_classification(
            model1_probs, model2_probs,
            model1_index_to_label,
            model2_index_to_label,
            alpha
        )

        y_true.append(true_label)
        y_pred.append(final_pred)

        prediction_rows.append({
            'image_path': img_path,
            'true_label': true_label,
            'predicted_label': final_pred
        })

    # Hitung metrik evaluasi
    acc = accuracy_score(y_true, y_pred)
    f1_macro = f1_score(y_true, y_pred, average='macro')
    f1_weighted = f1_score(y_true, y_pred, average='weighted')
    precision_macro = precision_score(y_true, y_pred, average='macro')
    recall_macro = recall_score(y_true, y_pred, average='macro')

    # Print classification report ke terminal
    print("\n📊 Classification Report:")
    print(classification_report(y_true, y_pred, digits=4))

    # Simpan hasil prediksi dan metrik ke CSV
    with open(output_csv, mode='w', newline='', encoding='utf-8') as f:
        fieldnames = ['image_path', 'true_label', 'predicted_label']
        writer = csv.DictWriter(f, fieldnames=fieldnames)
        writer.writeheader()
        writer.writerows(prediction_rows)

        # Baris kosong
        f.write('\n')

        # Tulis metrik evaluasi
        metrics_writer = csv.writer(f)
        metrics_writer.writerow(['metric', 'value'])
        metrics_writer.writerow(['accuracy', acc])
        metrics_writer.writerow(['f1_score_macro', f1_macro])
        metrics_writer.writerow(['f1_score_weighted', f1_weighted])
        metrics_writer.writerow(['precision_macro', precision_macro])
        metrics_writer.writerow(['recall_macro', recall_macro])

    print(f"\n✅ Hasil prediksi dan evaluasi disimpan di: {output_csv}")


# Contoh pemanggilan fungsi
predict_batch_and_evaluate(
    model1_val_dir='Datasets/model1/validation',
    model2_val_dir='Datasets/model2/validation',
    output_csv='hasil_prediksi_04.csv',
    alpha=0.4
)
predict_batch_and_evaluate(
    model1_val_dir='Datasets/model1/validation',
    model2_val_dir='Datasets/model2/validation',
    output_csv='hasil_prediksi_05.csv',
    alpha=0.5
)
predict_batch_and_evaluate(
    model1_val_dir='Datasets/model1/validation',
    model2_val_dir='Datasets/model2/validation',
    output_csv='hasil_prediksi_06.csv',
    alpha=0.6
)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━

/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 96ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 74ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━

/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 169ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━

/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/gaaf/thesis-ocr-aksara-sunda/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f